# Overview

This notebook uses pyapacheatlas to inject lineage between input and output assets 

In [1]:
pip install pyapacheatlas

Note: you may need to restart the kernel to use updated packages.


In [27]:
pip install snowflake-connector-python

Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install "snowflake-connector-python[pandas]"

     ---------------------------------------- 0.0/65.6 kB ? eta -:--:--
     ---------------------------------------- 65.6/65.6 kB 3.5 MB/s eta 0:00:00
   ---------------------------------------- 0.0/913.3 kB ? eta -:--:--
   -------------------------- ------------ 614.4/913.3 kB 12.9 MB/s eta 0:00:01
   ---------------------------------------- 913.3/913.3 kB 9.6 MB/s eta 0:00:00
   ---------------------------------------- 0.0/105.0 kB ? eta -:--:--
   ---------------------------------------- 105.0/105.0 kB 5.9 MB/s eta 0:00:00
   ---------------------------------------- 0.0/2.9 MB ? eta -:--:--
   ------- -------------------------------- 0.6/2.9 MB 17.3 MB/s eta 0:00:01
   ----------- ---------------------------- 0.8/2.9 MB 13.2 MB/s eta 0:00:01
   ---------------- ----------------------- 1.2/2.9 MB 9.6 MB/s eta 0:00:01
   ----------------------- ---------------- 1.7/2.9 MB 9.8 MB/s eta 0:00:01
   ------------------------------ --------- 2.2/2.9 MB 10.7 MB/s eta 0:00:01
   -----------


[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [6]:
pip install pandas

     ---------------------------------------- 0.0/60.9 kB ? eta -:--:--
     --------------------------------- ------ 51.2/60.9 kB ? eta -:--:--
     ---------------------------------------- 60.9/60.9 kB 1.1 MB/s eta 0:00:00
   ---------------------------------------- 0.0/11.5 MB ? eta -:--:--
   ---- ----------------------------------- 1.4/11.5 MB 18.0 MB/s eta 0:00:01
   -------- ------------------------------- 2.3/11.5 MB 12.4 MB/s eta 0:00:01
   --------- ------------------------------ 2.8/11.5 MB 10.5 MB/s eta 0:00:01
   ----------- ---------------------------- 3.3/11.5 MB 10.0 MB/s eta 0:00:01
   ------------- -------------------------- 4.0/11.5 MB 9.7 MB/s eta 0:00:01
   --------------- ------------------------ 4.5/11.5 MB 8.4 MB/s eta 0:00:01
   ---------------- ----------------------- 4.9/11.5 MB 8.2 MB/s eta 0:00:01
   ------------------- -------------------- 5.5/11.5 MB 8.0 MB/s eta 0:00:01
   -------------------- ------------------- 5.8/11.5 MB 7.4 MB/s eta 0:00:01
   -----


[notice] A new release of pip is available: 24.0 -> 24.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [5]:
# Install Atlas Python client (https://github.com/wjohnson/pyapacheatlas)
import pyapacheatlas
import json
import snowflake.connector
import pandas as pd
import uuid

from pyapacheatlas.core import AtlasEntity
from pyapacheatlas.core import AtlasProcess
from pyapacheatlas.auth import ServicePrincipalAuthentication
from pyapacheatlas.core import PurviewClient
from pyapacheatlas.core.collections import PurviewCollectionsClient
from pyapacheatlas.core.typedef import EntityTypeDef, AtlasAttributeDef
from pyapacheatlas.core.util import GuidTracker

In [3]:
import pandas as mc
import importlib

importlib.reload(mc)

<module 'pandas' from 'c:\\Users\\pidoudet\\AppData\\Local\\Programs\\Python\\Python312\\Lib\\site-packages\\pandas\\__init__.py'>

In [4]:
# Define variable

# SPN + Purview account
vTenantID = ""
vClientID = ""
vClientSecret = ""
vPurviewAccount = "pdedemopurv"

#Snowflake information
vUser=""
vPassword=""
vAccount= ""
vWarehouse="COMPUTE_WH"
vDatabase="TASTY_BYTES_SAMPLE_DATA"
vSchema="RAW_POS"

In [6]:


# enter your service principal credentials here
oauth = ServicePrincipalAuthentication(
    tenant_id= vTenantID,
    client_id=vClientID,
    client_secret=vClientSecret
)


conn = snowflake.connector.connect(
    user=vUser,
    password=vPassword,
    account=vAccount,
    warehouse=vWarehouse,
    database=vDatabase,
    schema=vSchema
    )

# Instantiate PurviewClient, enter your Purview account name here
client = PurviewClient(
    account_name =  vPurviewAccount,
    authentication=oauth
)

collection = PurviewCollectionsClient(
    endpoint_url =  "https://" + vPurviewAccount +".purview.azure.com/",
    authentication=oauth
)


In [11]:
#client.get_all_typedefs()

{'enumDefs': [{'category': 'ENUM',
   'guid': '6e30d01e-f5d0-9799-08e7-09b4f276c09c',
   'createdBy': 'admin',
   'updatedBy': 'admin',
   'createTime': 1725387243476,
   'updateTime': 1725387243476,
   'version': 1,
   'name': 'glossary_term_status_value',
   'description': 'glossary_term_status_value',
   'typeVersion': '1.0',
   'lastModifiedTS': '1',
   'elementDefs': [{'value': 'Approved', 'ordinal': 0},
    {'value': 'Alert', 'ordinal': 1},
    {'value': 'Expired', 'ordinal': 2},
    {'value': 'Draft', 'ordinal': 3}]},
  {'category': 'ENUM',
   'guid': '42185ddb-29be-e911-ea52-890154eb07c0',
   'createdBy': 'admin',
   'updatedBy': 'admin',
   'createTime': 1725387243475,
   'updateTime': 1725387243475,
   'version': 2,
   'name': 'AtlasGlossaryTermRelationshipStatus',
   'description': 'TermRelationshipStatus defines how reliable the relationship is between two glossary terms',
   'typeVersion': '1.1',
   'serviceType': 'atlas_core',
   'lastModifiedTS': '2',
   'elementDefs': [

In [7]:
# Check if the table exists in Purview
def check_entity_if_exist(client, qualifiedName, typeName):
    entities = client.get_entity(qualifiedName=qualifiedName, typeName=typeName)
    return len(entities) > 0

In [8]:
procType = EntityTypeDef(
    "ProcessCustomSnowflake",
    superTypes=["Process"],
    attributeDefs = [
        AtlasAttributeDef("columnMapping")
    ]
)

# Upload the type definition
type_results = client.upload_typedefs(entityDefs=[procType], force_update=True)
print(json.dumps(type_results,indent=2))

{
  "enumDefs": [],
  "structDefs": [],
  "classificationDefs": [],
  "entityDefs": [
    {
      "category": "ENTITY",
      "guid": "77a19aa1-5d9e-fb22-b544-ba12d5c1603d",
      "createdBy": "b239f754-726d-4331-b452-0155f65046fa",
      "updatedBy": "b239f754-726d-4331-b452-0155f65046fa",
      "createTime": 1726385724201,
      "updateTime": 1726387997959,
      "version": 2,
      "name": "ProcessCustomSnowflake",
      "description": "ProcessCustomSnowflake",
      "typeVersion": "1.0",
      "lastModifiedTS": "2",
      "attributeDefs": [
        {
          "name": "columnMapping",
          "typeName": "string",
          "isOptional": true,
          "cardinality": "SINGLE",
          "valuesMinCount": 0,
          "valuesMaxCount": 1,
          "isUnique": false,
          "isIndexable": false,
          "includeInNotification": false
        }
      ],
      "superTypes": [
        "Process"
      ],
      "subTypes": [],
      "relationshipAttributeDefs": [
        {
      

In [41]:
cur = conn.cursor()

# Execute a statement that will generate a result set.
sql = f"""SELECT
        S.TABLE_CATALOG as SourceCatalog,
        S.TABLE_SCHEMA as SourceSchema,
        S.TABLE_NAME as SourceTable,
        S.COLUMN_NAME as SourceColumn,
        S.DATA_TYPE as SourceColumnType,
        T.TABLE_CATALOG as TargetCatalog,
        T.TABLE_SCHEMA as TargetSchema,
        T.TABLE_NAME as TargetTable,
        T.COLUMN_NAME as TargetColumn,
        T.DATA_TYPE as TargetColumnType
   FROM SNOWFLAKE_SAMPLE_DATA.INFORMATION_SCHEMA.COLUMNS S
   JOIN SNOWFLAKE_SAMPLE_DATA.INFORMATION_SCHEMA.COLUMNS T ON S.TABLE_NAME = T.TABLE_NAME AND S.COLUMN_NAME = T.COLUMN_NAME
   WHERE S.TABLE_SCHEMA = 'TPCDS_SF10TCL' AND T.TABLE_SCHEMA = 'TPCDS_SF100TCL'"""

cur.execute(sql)

# Fetch the result set from the cursor and deliver it as the pandas DataFrame.
df = cur.fetch_pandas_all()
#print(df)
jsonSchema = []
df = df.sort_values(by=["SOURCECATALOG","SOURCESCHEMA","SOURCETABLE","SOURCECOLUMN"], ascending=True)
tables = df.groupby(["SOURCETABLE","TARGETTABLE"]).groups

for rec in tables:
    SourceTableName=rec[0]
    TargetTableName=rec[1]
    
    
    SourceQualifiedName= f"""snowflake://https/databases/SNOWFLAKE_SAMPLE_DATA/schemas/TPCDS_SF10TCL/tables/{SourceTableName}"""
    TargetQualifiedName= f"""snowflake://https/databases/SNOWFLAKE_SAMPLE_DATA/schemas/TPCDS_SF100TCL/tables/{TargetTableName}"""
    #print(SourceQualifiedName)

    if check_entity_if_exist(client, SourceQualifiedName, "snowflake_table"):
        SourceLineage = AtlasEntity(
            name=SourceTableName,
            typeName="snowflake_table",
            qualified_name=SourceQualifiedName,
            #guid=str(uuid.uuid4())
        )
    if check_entity_if_exist(client, TargetQualifiedName, "snowflake_table"):
        TargetLineage = AtlasEntity(
            name=TargetTableName,
            typeName="snowflake_table",
            qualified_name=TargetQualifiedName,
            #guid=str(uuid.uuid4())
        )

    ListMapping = []
    columns = df[(df["SOURCETABLE"] == SourceTableName) & (df["TARGETTABLE"] == TargetTableName)].groupby(["SOURCECOLUMN","SOURCECOLUMNTYPE","TARGETCOLUMN","TARGETCOLUMNTYPE"]).groups
    #print(columns)  
    for SOURCECOLUMN,SOURCECOLUMNTYPE, TARGETCOLUMN,TARGETCOLUMNTYPE in columns:
        #print(SOURCECOLUMN)
        ListMapping.append({"Source": f"{SOURCECOLUMN}", "Sink": f"{TARGETCOLUMN}"})
      
    #print(ListMapping)
    column_mapping = [
        # This object defines the column lineage between input01 and output01
        {"ColumnMapping": ListMapping,
            "DatasetMapping": {
            "Source": SourceLineage.qualifiedName, "Sink": TargetLineage.qualifiedName}
        }
    ]
    print(column_mapping)
    #Custom Process for Snowflake with Column Lineage
    process_qn = f"""snowflake://sqlqueryfrom{SourceTableName}to{TargetTableName}"""
    process_type_name = "ProcessCustomSnowflake"

    vuuid = "-"+ str(uuid.uuid4())
    process = AtlasProcess(
        name="Snowflake query",
        typeName=process_type_name,
        qualified_name=process_qn,
        inputs=[SourceLineage],
        outputs=[TargetLineage],
        guid=vuuid,
        attributes={"columnMapping": json.dumps(column_mapping)}
    )
    results = client.upload_entities(batch=[process])

[{'ColumnMapping': [{'Source': 'CC_CALL_CENTER_ID', 'Sink': 'CC_CALL_CENTER_ID'}, {'Source': 'CC_CALL_CENTER_SK', 'Sink': 'CC_CALL_CENTER_SK'}, {'Source': 'CC_CITY', 'Sink': 'CC_CITY'}, {'Source': 'CC_CLASS', 'Sink': 'CC_CLASS'}, {'Source': 'CC_CLOSED_DATE_SK', 'Sink': 'CC_CLOSED_DATE_SK'}, {'Source': 'CC_COMPANY', 'Sink': 'CC_COMPANY'}, {'Source': 'CC_COMPANY_NAME', 'Sink': 'CC_COMPANY_NAME'}, {'Source': 'CC_COUNTRY', 'Sink': 'CC_COUNTRY'}, {'Source': 'CC_COUNTY', 'Sink': 'CC_COUNTY'}, {'Source': 'CC_DIVISION', 'Sink': 'CC_DIVISION'}, {'Source': 'CC_DIVISION_NAME', 'Sink': 'CC_DIVISION_NAME'}, {'Source': 'CC_EMPLOYEES', 'Sink': 'CC_EMPLOYEES'}, {'Source': 'CC_GMT_OFFSET', 'Sink': 'CC_GMT_OFFSET'}, {'Source': 'CC_HOURS', 'Sink': 'CC_HOURS'}, {'Source': 'CC_MANAGER', 'Sink': 'CC_MANAGER'}, {'Source': 'CC_MARKET_MANAGER', 'Sink': 'CC_MARKET_MANAGER'}, {'Source': 'CC_MKT_CLASS', 'Sink': 'CC_MKT_CLASS'}, {'Source': 'CC_MKT_DESC', 'Sink': 'CC_MKT_DESC'}, {'Source': 'CC_MKT_ID', 'Sink': 'CC_